In [1]:
import os
import itertools
import math
import numpy as np
import pandas as pd
import requests
import pickle
from datetime import datetime as dt
from datetime import timedelta
import pytz
from pytz import timezone
from pprint import pprint
import pandas_datareader.data as web
from collections import namedtuple
from operator import itemgetter

import cufflinks as cf
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import yfinance as yf
import fundamentalanalysis as fa
import streamlit as st

import pandas_datareader.data as web
import yahoo_fin.stock_info as si
from urllib.request import Request, urlopen
from html_table_parser.parser import HTMLTableParser 
import streamlit as st

from load_data import *
from get_data import get_tickers

pd.options.plotting.backend = "plotly"


In [2]:
rf_rates = get_rf_data()
SPY_df = get_SPY_data()
SPY_info_df = get_SPY_info()
ticker_info = get_ticker_info()
ticker_list = SPY_info_df.index.to_list()
sector_list = SPY_info_df['Sector'].unique()
first_date = SPY_df.iloc[0].name
last_date = SPY_df.iloc[-1].name
yr_ago = last_date - timedelta(days=365)
# TTM_ratios, ratios_data_report = load_TTM_ratios()

In [3]:
df2 = pd.read_csv(r'data\spy_data\SPY_Historical.csv', index_col='Date')
df2

Ticker                        Security  inSPY
Date                                                    
2023-01-05    VNO            Vornado Realty Trust  False
2023-01-04   GEHC                   GE HealthCare   True
2022-12-22   ABMD                         Abiomed  False
2022-12-22   STLD                  Steel Dynamics   True
2022-12-19   FBHS  Fortune Brands Home & Security  False
...           ...                             ...    ...
1998-12-11   CPWR                       Compuware   True
1998-12-11    CCL                  Carnival Corp.   True
1998-12-11    FSR                         Firstar   True
1997-06-17    CCI   Countrywide Credit Industries   True
1997-06-17    USL                          USLife  False

[617 rows x 3 columns]

In [4]:
def get_removed_market_data():  
    '''Get historical data for tickers removed from S&P 500'''

    tickers = get_tickers()[1]
    n = len(tickers)
    not_downloaded = []
    path = r'data\removed_from_index\market_data'

    for i, ticker in enumerate(tickers, 1):
        try:
            fname = os.path.join(path, f'{ticker}.csv')
            df = si.get_data(ticker) # download stock data
            df.to_csv(fname)
            print(f"\r{i}/{n} ({i / n:.2%}) of removed SPY market data downloaded",
                  end='', flush=True)
        except Exception as e:
            # print(f'\r{i}/{n}: {ticker} - {e}')
            not_downloaded.append(ticker)  

    print('\nS&P 500 removed stock data downloaded \n')

    if not_downloaded:
        print(f'{len(not_downloaded)} stocks not downloaded \n')
    
    return not_downloaded

In [3]:
tickers, hist_tickers = get_tickers()
# hist_tickers = set(hist_tickers) - set(tickers)
len(hist_tickers)

306

In [4]:
path = r'data\removed_from_index\market_data'
hist_tickers = [os.path.splitext(f)[0] for f in os.listdir(path)]
print(len(hist_tickers))
# hist_tickers

185


In [14]:
ticker_info['ABMD']

{'Security': 'N/A',
 'Sector': 'N/A',
 'Industry': 'N/A',
 'Business Summary': 'N/A',
 'Website': 'N/A'}

In [107]:
securities_list = fa.available_companies('a812dc7d35321ed0502ea50d8dc71be9')

In [108]:
len(securities_list)

67339

In [5]:
securities_list['type'].unique()

array(['etf', 'stock', 'trust', 'fund'], dtype=object)

In [6]:
securities_list[securities_list['type'] == 'etf']

name   price  \
symbol                                               
SPY                 SPDR S&P 500 ETF Trust  396.91   
GDX                 VanEck Gold Miners ETF   24.19   
EEM      iShares MSCI Emerging Markets ETF   38.25   
XLF      Financial Select Sector SPDR Fund   33.74   
EFA                  iShares MSCI EAFE ETF   60.49   
...                                    ...     ...   
ASOL.SW        21Shares Solana staking ETP   19.08   
AVAX.SW             21Shares Avalanche ETP    3.63   
ABNB.SW           21Shares Binance BNB ETP   20.12   
TDT.AS                VanEck AEX UCITS ETF   67.44   
TMX.AS                VanEck AMX UCITS ETF   91.94   

                             exchange exchangeShortName type  
symbol                                                        
SPY      New York Stock Exchange Arca              AMEX  etf  
GDX      New York Stock Exchange Arca              AMEX  etf  
EEM      New York Stock Exchange Arca              AMEX  etf  
XLF      New York Stock Exchange Arca              AMEX  etf  
EFA      New York Stock Exchange Arca              AMEX  etf  
...                               ...               ...  ...  
ASOL.SW                Swiss Exchange               SIX  etf  
AVAX.SW                Swiss Exchange               SIX  etf  
ABNB.SW                Swiss Exchange               SIX  etf  
TDT.AS                      Amsterdam               AMS  etf  
TMX.AS                      Amsterdam               AMS  etf  

[5798 rows x 5 columns]

## Technical Analysis

In [6]:
df = get_ticker_data('tsla')
end = dt.now()
years = 1
start = end - timedelta(365 * years)
print(end)

2023-01-31 19:45:49.280277


In [7]:
def isSupport(df, i):
    '''Returns True if value is a price support level'''

    X = df['Low']
    support = X[i] < X[i - 1] \
                and X[i] < X[i + 1] \
                and X[i + 1] < X[i + 2] \
                and X[i - 1] < X[i - 2]

    return support


def isResistance(df, i):
    '''Returns True if value is a price resistance level'''

    X = df['High']
    resistance = X[i] > X[i - 1] \
                    and X[i] > X[i + 1] \
                    and X[i + 1] > X[i + 2] \
                    and X[i - 1] > X[i - 2] 

    return resistance
    

In [8]:
def sr_levels(df, start, end):
    '''Returns key support/resistance levels for a security'''

    df = df[start : end]
    levels = []
    s = (df['High'] - df['Low']).mean()

    def isFarFromLevel(l):
        '''
        Given a price value, returns False 
        if it is near some previously discovered key level
        '''
        
        return np.sum([abs(l - x[2]) < s for x in levels]) == 0

    for i in range(2, df.shape[0]-2):
        low = df['Low'][i]
        high = df['High'][i]

        if isSupport(df, i):
            name = 'Support'
            if isFarFromLevel(low):
                levels.append((name, i, low))
        elif isResistance(df, i):
            name = 'Resistance'
            if isFarFromLevel(high):
                levels.append((name, i, high))

    return levels

In [9]:
def sr_analysis(df, levels):
    start = df.iloc[0].name
    
    for c, i, l in levels:
        ix = df.iloc[i].name
        print(f'{c}, {ix.date()}, {l:,.2f}')

    
    

In [10]:
def calculate_trends(ticker, start, end, time_frame, short_ma, inter_ma, long_ma):
    df = get_ticker_data(ticker)[start : end]
    df.columns = df.columns.str.title()
    df.drop(columns=['Ticker', 'Adjclose'], inplace=True)

    if time_frame != 'Daily':
        if time_frame == 'Weekly':
            fmt = 'W-MON'
        elif time_frame == 'Monthly':
            fmt = 'BMS'

        ix = df.asfreq(fmt).index
        open_ = df['Open'].resample(fmt).first()
        close = df['Close'].resample(fmt).last()
        high = df['High'].resample(fmt).max()
        low = df['Low'].resample(fmt).min()
        volume = df['Volume'].resample(fmt).sum()
        d = dict(Open=open_, High=high, Low=low, Close=close, Volume=volume)
        df = pd.DataFrame(d, index=ix)

    df[f'MA{short_ma}'] = df['Close'].rolling(short_ma).mean()
    df[f'MA{inter_ma}'] = df['Close'].rolling(inter_ma).mean()
    df[f'MA{long_ma}'] = df['Close'].rolling(long_ma).mean()

    if time_frame == 'Daily':
        confirm_ma = 200
        df[f'MA{confirm_ma}'] = df['Close'].rolling(confirm_ma).mean()

    levels = sr_levels(df, start, end)
    sr_analysis(df, levels)

    return df

In [11]:
ticker = 'amzn'
df = get_ticker_data(ticker)
end = dt.now()
years = 1
start = end - timedelta(365 * years)
time_frame, short_ma, inter_ma, primary_ma = 'Daily', 10, 20, 50

In [12]:
ta_df = calculate_trends(ticker, start, end, time_frame, short_ma, inter_ma, primary_ma)
ta_df.tail(10)

Support, 2022-02-14, 151.65
Resistance, 2022-02-17, 160.35
Support, 2022-02-24, 139.50
Support, 2022-03-08, 133.57
Resistance, 2022-03-29, 170.83
Support, 2022-05-12, 102.41
Resistance, 2022-05-17, 115.80
Resistance, 2022-07-22, 125.50
Resistance, 2022-08-16, 146.57
Support, 2022-11-09, 85.87
Support, 2022-11-21, 90.59
Resistance, 2022-12-01, 97.23
Support, 2023-01-06, 81.43


Open        High        Low       Close    Volume  \
2023-01-17   98.680000   98.889999  95.730003   96.050003  72755000   
2023-01-18   97.250000   99.320000  95.379997   95.459999  79570400   
2023-01-19   94.739998   95.440002  92.860001   93.680000  69002700   
2023-01-20   93.860001   97.349998  93.199997   97.250000  67307100   
2023-01-23   97.559998   97.779999  95.860001   97.519997  76501100   
2023-01-24   96.930000   98.089996  96.000000   96.320000  66929500   
2023-01-25   92.559998   97.239998  91.519997   97.180000  94261600   
2023-01-26   98.239998   99.489998  96.919998   99.220001  68523600   
2023-01-27   99.529999  103.489998  99.529999  102.239998  87678100   
2023-01-30  101.089996  101.739998  99.010002  100.550003  70566100   

                 MA10     MA20     MA50       MA200  
2023-01-17  90.192001  87.4370  90.6520  115.678803  
2023-01-18  91.156001  87.8170  90.7752  115.341115  
2023-01-19  92.010001  88.2550  90.8292  114.991715  
2023-01-20  93.423000  88.8580  90.9636  114.636233  
2023-01-23  94.567000  89.3955  91.1144  114.303558  
2023-01-24  95.463000  90.0220  91.3180  113.991378  
2023-01-25  96.193999  90.6185  91.3290  113.688355  
2023-01-26  96.607000  91.4275  91.2976  113.412153  
2023-01-27  97.304000  92.4485  91.3726  113.167743  
2023-01-30  97.547000  93.2670  91.4048  112.916555

In [22]:
def sr_levels(df, start, end):
    '''Returns key support/S-R levels for a security'''

    df = df[start : end]
    df.columns = df.columns.str.title()
    df.drop(columns=['Ticker', 'Adjclose'], inplace=True)
    support = []
    resistance = []
    levels = []
    s = (df['High'] - df['Low']).mean()

    def isFarFromLevel(l):
        '''
        Given a price value, returns False 
        if it is near some previously discovered key level
        '''
        
        # levels = support + resistance
        return np.sum([abs(l - x[1]) < s for x in levels]) == 0

    for i in range(2, df.shape[0] - 2):
        sprev = start if not support else df.iloc[support[-1][0]].name
        rprev = start if not resistance else df.iloc[resistance[-1][0]].name
        prev = start if not levels else df.iloc[levels[-1][0]].name
        ix = df.iloc[i].name
        high = df.loc[ix, 'High']
        low = df.loc[ix, 'Low']
        d = pd.Timedelta(ix - prev).days # days it takes level to form

        if isSupport(df, i):
            l = df['Low'][i]
            if isFarFromLevel(l):
                # d = pd.Timedelta(ix - sprev).days # days it takes level to form
                support.append((i, l, d))
                levels.append((i, l, d))
                n_spt = 0
                df.loc[ix:, 'Support'] = l
                df.loc[ix, 'S-R Formation (Days)'] = d
                df.loc[ix, 'S-R Volume'] = df.loc[prev: ix, 'Volume'].sum()
                df.loc[ix, 'S-R Tests'] = n_spt
                print(f'Support: {l:,.2f} formed on {ix.date()} took {d} days to form')
        elif isResistance(df, i):
            l = df['High'][i]
            if isFarFromLevel(l):
                # d = pd.Timedelta(ix - rprev).days # days it takes level to form
                resistance.append((i, l, d))
                levels.append((i, l, d))
                n_rst = 0
                df.loc[ix:, 'Resistance'] = l
                df.loc[ix, 'S-R Formation (Days)'] = d
                df.loc[ix, 'S-R Volume'] = df.loc[prev: ix, 'Volume'].sum()
                df.loc[ix, 'S-R Tests'] = n_rst
                print(f'Resistance: {l:,.2f} formed on {ix.date()} took {d} days to form')
        
        if support and resistance:
            s_ix, spt, sd = support[-1]
            r_ix, rst, rd = resistance[-1]
            sdt = df.iloc[s_ix].name
            rdt = df.iloc[r_ix].name
            
            # Support tested
            if high >= spt and low <= spt:
                n_spt += 1
                row = df.iloc[s_ix].name
                df.loc[row, 'S-R Tests'] = n_spt
                print(f'{ix.date()}, Support: {spt:,.2f}, Tests: {n_spt}, Formed: {sdt.date()}, Delta: {sd}')
            
            # Resistance tested
            if high >= rst and low <= rst:
                n_rst += 1
                row = df.iloc[r_ix].name
                df.loc[row, 'S-R Tests'] = n_rst
                print(f'{ix.date()}, Resistance: {rst:,.2f}, Tests: {n_rst}, Formed: {rdt.date()}, Delta: {rd}')
            
            # STILL NEEDS WORK, formation calcns are off
            # Support becomes resistance
            # if high < spt:
            #     d = pd.Timedelta(ix - rdt).days
            #     df.loc[ix:, 'Resistance'] = spt
            #     df.loc[ix, 'S-R Formation (Days)'] = d
            #     resistance.append((i, spt, d))
            #     print(f'{ix.date()}, R - S: {rst:,.2f}, Formed: {rdt.date()}, Delta: {d}')
            
            # # Resistance becomes support
            # if low > rst:
            #     d = pd.Timedelta(ix - sdt).days
            #     df.loc[ix:, 'Support'] = rst
            #     df.loc[ix, 'S-R Formation (Days)'] = d
            #     support.append((i, rst, d))
            #     print(f'{ix.date()}, S - R: {spt:,.2f}, Formed: {sdt.date()}, Delta: {d}')

            
            # print(spt, rst)
            # rst = spt

    cols = ['Support', 'Resistance', 'S-R Formation (Days)', 'S-R Volume', 'S-R Tests']
    cols = df.columns[:-5].to_list() + cols
    df = df[cols]
                  
    return support, resistance, df


In [23]:
support, resistance, ta_df = sr_levels(df, start, end)

Support: 151.65 formed on 2022-02-14 took 13 days to form
Resistance: 160.35 formed on 2022-02-17 took 3 days to form
2022-02-17, Resistance: 160.35, Tests: 1, Formed: 2022-02-17, Delta: 3
2022-02-18, Support: 151.65, Tests: 1, Formed: 2022-02-14, Delta: 13
2022-02-22, Support: 151.65, Tests: 2, Formed: 2022-02-14, Delta: 13
2022-02-23, Support: 151.65, Tests: 3, Formed: 2022-02-14, Delta: 13
Support: 139.50 formed on 2022-02-24 took 7 days to form
2022-02-24, Support: 139.50, Tests: 1, Formed: 2022-02-24, Delta: 7
2022-03-07, Support: 139.50, Tests: 2, Formed: 2022-02-24, Delta: 7
Support: 133.57 formed on 2022-03-08 took 12 days to form
2022-03-08, Support: 133.57, Tests: 1, Formed: 2022-03-08, Delta: 12
2022-03-18, Resistance: 160.35, Tests: 2, Formed: 2022-02-17, Delta: 3
2022-03-21, Resistance: 160.35, Tests: 3, Formed: 2022-02-17, Delta: 3
2022-03-24, Resistance: 160.35, Tests: 4, Formed: 2022-02-17, Delta: 3
Resistance: 170.83 formed on 2022-03-29 took 21 days to form
2022-03-29

In [24]:
ta_df.tail(50)

Open        High        Low       Close     Volume  \
2022-11-16   96.849998   98.489998  95.540001   97.120003   87958800   
2022-11-17   95.370003   96.970001  94.029999   94.849998   82617900   
2022-11-18   95.949997   95.989998  92.480003   94.139999   72428200   
2022-11-21   93.970001   95.019997  90.589996   92.459999   84330300   
2022-11-22   92.620003   93.349998  90.870003   93.199997   62192000   
2022-11-23   93.239998   94.580002  92.830002   94.129997   59414700   
2022-11-25   93.790001   94.430000  93.070000   93.410004   35088600   
2022-11-28   93.930000   96.400002  93.430000   93.949997   74943100   
2022-11-29   94.040001   94.410004  91.440002   92.419998   65567300   
2022-11-30   92.470001   96.540001  91.529999   96.540001  102805800   
2022-12-01   96.989998   97.230003  94.919998   95.500000   68488000   
2022-12-02   94.480003   95.360001  93.779999   94.129997   72496400   
2022-12-05   93.050003   94.059998  90.820000   91.010002   71535500   
2022-12-06   90.500000   91.040001  87.900002   88.250000   75503600   
2022-12-07   88.339996   89.889999  87.480003   88.459999   68086900   
2022-12-08   89.239998   90.860001  87.879997   90.349998   73305900   
2022-12-09   88.900002   90.300003  88.629997   89.089996   67398500   
2022-12-12   89.209999   90.580002  87.870003   90.550003   61999800   
2022-12-13   95.230003   96.250000  90.519997   92.489998  100212000   
2022-12-14   92.500000   93.459999  89.870003   91.580002   70298000   
2022-12-15   89.889999   89.970001  87.470001   88.449997   84802900   
2022-12-16   88.269997   89.349998  86.730003   87.860001  146144100   
2022-12-19   87.510002   87.629997  84.510002   84.919998   83531500   
2022-12-20   85.330002   86.610001  84.330002   85.190002   74348300   
2022-12-21   86.180000   87.230003  85.209999   86.769997   59267200   
2022-12-22   85.519997   85.680000  82.250000   83.790001   81431300   
2022-12-23   83.250000   85.779999  82.930000   85.250000   57433700   
2022-12-27   84.970001   85.349998  83.000000   83.040001   57284000   
2022-12-28   82.800003   83.480003  81.690002   81.820000   58228600   
2022-12-29   82.870003   84.550003  82.550003   84.180000   54995900   
2022-12-30   83.120003   84.050003  82.470001   84.000000   62330000   
2023-01-03   85.459999   86.959999  84.209999   85.820000   76706000   
2023-01-04   86.550003   86.980003  83.360001   85.139999   68885100   
2023-01-05   85.330002   85.419998  83.070000   83.120003   67930800   
2023-01-06   83.029999   86.400002  81.430000   86.080002   83219100   
2023-01-09   87.459999   89.480003  87.080002   87.360001   65266100   
2023-01-10   87.570000   90.190002  87.290001   89.870003   67756600   
2023-01-11   90.930000   95.260002  90.930000   95.089996  103126200   
2023-01-12   96.930000   97.190002  93.500000   95.269997   85254800   
2023-01-13   94.180000   98.370003  94.120003   98.120003   85413600   
2023-01-17   98.680000   98.889999  95.730003   96.050003   72755000   
2023-01-18   97.250000   99.320000  95.379997   95.459999   79570400   
2023-01-19   94.739998   95.440002  92.860001   93.680000   69002700   
2023-01-20   93.860001   97.349998  93.199997   97.250000   67307100   
2023-01-23   97.559998   97.779999  95.860001   97.519997   76501100   
2023-01-24   96.930000   98.089996  96.000000   96.320000   66929500   
2023-01-25   92.559998   97.239998  91.519997   97.180000   94261600   
2023-01-26   98.239998   99.489998  96.919998   99.220001   68523600   
2023-01-27   99.529999  103.489998  99.529999  102.239998   87678100   
2023-01-30  101.089996  101.739998  99.010002  100.550003   70566100   

              Support  Resistance  S-R Formation (Days)    S-R Volume  \
2022-11-16  85.870003  146.570007                   NaN           NaN   
2022-11-17  85.870003  146.570007                   NaN           NaN   
2022-11-18  85.870003  146.570007                   NaN           NaN   
2022-11-21  90.589996  146.570007                  12

In [119]:
ta_df.loc[start, 'Resistance'].notna()

KeyError: datetime.datetime(2022, 1, 31, 17, 48, 31, 465269)

In [166]:
def calculate_trends(ticker, start, end, time_frame, short_ma, inter_ma, primary_ma):
    df = get_ticker_data(ticker)[start : end]
    df.drop(columns=['ticker', 'adjclose'], axis=1, inplace=True)
    df.columns = df.columns.str.title()  

    if time_frame != 'Daily':
        if time_frame == 'Weekly':
            fmt = 'W-MON'
        elif time_frame == 'Monthly':
            fmt = 'BMS'

        ix = df.asfreq(fmt).index
        open_ = df['Open'].resample(fmt).first()
        close = df['Close'].resample(fmt).last()
        high = df['High'].resample(fmt).max()
        low = df['Low'].resample(fmt).min()
        volume = df['Volume'].resample(fmt).sum()
        d = dict(Open=open_, High=high, Low=low, Close=close, Volume=volume)
        df = pd.DataFrame(d, index=ix)

    support, resistance, df = sr_levels(df, start, end)
    levels = support + resistance

    df[f'MA{short_ma}'] = df['Close'].rolling(short_ma).mean()
    df[f'MA{inter_ma}'] = df['Close'].rolling(inter_ma).mean()
    df[f'MA{primary_ma}'] = df['Close'].rolling(primary_ma).mean()

    # for s,r in itertools.zip_longest(support, resistance):
    #     print(s,r)

    # for row in df.index:
    #     # row = df.iloc[i].name
    #     low = df.loc[row, 'Low']
    #     high = df.loc[row, 'High']
    #     support = df.loc[row, 'Support']
    #     resistance = df.loc[row, 'Resistance']
        # print(row, low, high, support, resistance)
        # if low > resistance:
        #     print(f'R - S: {row.date()}')
        #     # print(f'resistance: {resistance}')
        #     support = resistance
        # if high < support:
        #     print(f'S - R: {row.date()}')
        #     resistance = support

    return df, levels

In [183]:
ta_df.loc['2021-04-14', ['High', 'Low', 'Support', 'Resistance']]

High          260.263336
Low           242.676666
Support       240.369995
Resistance    240.369995
Name: 2021-04-14 00:00:00, dtype: float64

In [175]:
# # pd.set_option('display.max_rows', None)
# support, resistance, ta_df = sr_levels(df, start, end)
# ta_df.iloc[short_ma:]

C:\Users\pnjor\AppData\Local\Temp\ipykernel_9236\4069413257.py:1: FutureWarning:

this method is deprecated in favour of `Styler.format(precision=..)`



In [97]:
SPY_info_df[SPY_info_df['Security'] == '3M'].index.item()

'MMM'

In [87]:
def plot_trends(df, start, end, time_frame, short_ma, inter_ma, primary_ma):
    '''
    Returns candlestick chart with support/resistance levels
    and market cycle trend lines

    Parameters
    ----------
    df: DataFrame of a security's market data
    start: Start Date
    end: End Date
    time_frame: [Daily, Weekly, Monthly]
    short_ma: moving average window
    inter_ma: moving average window
    primary_ma: moving average window
    '''

    df, levels = calculate_trends(df, start, end, time_frame, short_ma, inter_ma, primary_ma)
    name = df['Ticker'][0] if 'Ticker' in df.columns else ''
    cname = SPY_info_df.loc[name, 'Security']
    title1 = f'{cname}' # {time_frame} Trends & Support-Resistance Levels <br>
    title2 = ''

    fig = make_subplots(rows=2, cols=1,
                        shared_xaxes=True, 
                        vertical_spacing=0.01,
                        subplot_titles=(title1, title2), 
                        row_width=[0.2, 0.7])
    cs = go.Candlestick(x=df.index, 
                        open=df['Open'], 
                        high=df['High'],
                        low=df['Low'], 
                        close=df['Close'],
                        name=name)
    cs.increasing.fillcolor = 'green'
    cs.increasing.line.color = 'darkgreen'
    cs.decreasing.fillcolor = 'red'
    cs.decreasing.line.color = 'indianred'

    sma1 = go.Scatter(x=df.index, 
                      y=df[f'MA{short_ma}'], 
                      name=f'Short-Term Trend (MA{short_ma})',
                      line_width=1.25,
                      line_color='orange',
                      )
    sma2 = go.Scatter(x=df.index,
                      y=df[f'MA{inter_ma}'],
                      name=f'Intermediate Trend (MA{inter_ma})',
                      line_width=1.25)
    sma3 = go.Scatter(x=df.index,
                      y=df[f'MA{primary_ma}'],
                      name=f'Primary Trend (MA{primary_ma})',
                      line_width=1.25,
                      line_color='purple')
    
    fig.add_traces(data=[cs, sma1, sma2, sma3], rows=[1, 1, 1, 1], cols=[1, 1, 1, 1])   

    # Add support & resistance lines
    for i, l, d in levels:
        n = df.shape[0] - i
        fig.add_scatter(x=df.index[i:],
                        y=[l] * n,
                        name='S-R',
                        line={'color': 'blue', 'width': 0.5},
                        mode='lines',
                        showlegend=False)
        
    # Volume subplot
    fig.add_trace(go.Bar(x=df.index, y=df['Volume'], name='Volume'),
                  row=2, col=1)
    fig.update_xaxes(showgrid=False)              
    fig.update_yaxes(showgrid=False)
    fig.layout.annotations[0].update(x=0.015)
    fig.layout.xaxis.rangeslider.visible = False

    return fig

In [91]:
plot_trends(df, start, end, time_frame, short_ma, inter_ma, primary_ma)

Resistance: 64.59933471679688 formed on 2020-02-04 took 6 days to form
Support: 45.79999923706055 formed on 2020-02-06 took 8 days to form
Support: 23.367332458496094 formed on 2020-03-18 took 41 days to form
Resistance: 95.3000030517578 formed on 2020-07-07 took 154 days to form
Resistance: 119.66600036621094 formed on 2020-07-13 took 6 days to form
Resistance: 167.49667358398438 formed on 2020-09-01 took 50 days to form
Resistance: 153.97999572753906 formed on 2020-09-15 took 14 days to form
Support: 139.68333435058594 formed on 2020-10-20 took 216 days to form
Resistance: 202.6000061035156 formed on 2020-11-30 took 76 days to form
Resistance: 218.10667419433597 formed on 2020-12-09 took 9 days to form
Support: 188.77999877929688 formed on 2020-12-10 took 51 days to form
Resistance: 231.6666717529297 formed on 2020-12-18 took 9 days to form
Support: 260.0333251953125 formed on 2021-01-29 took 50 days to form
Resistance: 292.5899963378906 formed on 2021-02-08 took 52 days to form
Resi